In [1]:
from DATA225utils import make_connection, dataframe_query

In [2]:
conn = make_connection(config_file = 'ZAGI-sales.ini')
cursor = conn.cursor()

### **1.** Display the region ID, region name, and number of stores in the region for all regions.

In [3]:
_, df = dataframe_query(conn,
    """
    SELECT r.region_id, r.region_name, count(*)
    FROM region r, store s
    WHERE r.region_id = s.region_id
    GROUP BY r.region_id, r.region_name
    """
                       )

df

region_id  region_name  count(*)
0         C  Chicagoland         2
1         T     Tristate         1

### **2.** For each product category, display the category ID, category name, and average price of a product in the category.

In [4]:
_, df = dataframe_query(conn,
    """
    SELECT c.category_id, c.category_name, avg(p.product_price)
    FROM product p, category c
    WHERE p.category_id = c.category_id
    GROUP BY c.category_id, c.category_name
    """
                       )

df

category_id category_name avg(p.product_price)
0          CP       Camping           166.666667
1          FW      Footwear            58.333333

### **3.** For each product category, display the category ID and the total number of items purchased in the category.

In [5]:
_, df = dataframe_query(conn,
    """
    SELECT p.category_id, sum(s.no_of_items)
    FROM sold_via s, product p
    WHERE s.product_id = p.product_id
    GROUP BY p.category_id
    """
                       )

df

category_id sum(s.no_of_items)
0          CP                  5
1          FW                 13

### **4.** Display the TID and the total number of items (of all products) sold within the transaction for all sales transactions whose total number of items (of all products) sold within the transaction is greater than five.

In [6]:
_, df = dataframe_query(conn,
    """
    SELECT tid, SUM(no_of_items)
    FROM sold_via
    GROUP BY tid
    HAVING SUM(no_of_items) > 5
    """
                       )

df

tid SUM(no_of_items)
0  T333                6
1  T555                7

### **5.** Display the product ID and ProductName of the cheapest product.

In [7]:
_, df = dataframe_query(conn,
    """
    SELECT product_id, product_name
    FROM product
    WHERE product_price = (SELECT MIN(product_price)
                           FROM product)
    """
                       )

df

product_id product_name
0        3X3    Cosy Sock

### **6.** Display the product ID for the product that has been sold the most (i.e., that has been sold in the highest quantity).

#### The following query works with most versions of SQL. The nested SELECT in the HAVING clause selects the highest number of product sales.

In [8]:
_, df = dataframe_query(conn,
    """
    SELECT product_id
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = (SELECT MAX(SUM(no_of_items))
                               FROM sold_via
                               GROUP BY product_id)
    """
                       )

df

Exception: Query failed: 1111 (HY000): Invalid use of group function

#### Could the problem here be with the nested SELECT?

In [9]:
_, df = dataframe_query(conn,
    """
    SELECT MAX(SUM(no_of_items))
    FROM sold_via
    GROUP BY product_id
    """
                       )

df

Exception: Query failed: 1111 (HY000): Invalid use of group function

#### Yes, that's where the problem is. MySQL apparently doesn't like the combination MAX(SUM(no_of_items)) in the SELECT. No, I don't know why MySQL is missing certain features. 

#### So let's find the highest product sales in another way. First, what are the number of sales per product?

In [10]:
# Query A

_, df = dataframe_query(conn,
    """
    SELECT product_id, sum(no_of_items) AS total_sales
    FROM sold_via
    GROUP BY product_id
    """
                       )

df

product_id total_sales
0        1X1           2
1        2X2           3
2        3X3           5
3        4X4           5
4        5X5           2
5        6X6           1

#### We need to treat the above results as a **virtual table**. MySQL insists that we give it a name, so we can call it `total_sales_table`. Then we can select the maximum from the `total_sales` column.

In [11]:
# Query B

_, df = dataframe_query(conn,
    """
    SELECT max(total_sales) AS highest_sales
    FROM (SELECT sum(no_of_items) AS total_sales
          FROM sold_via
          GROUP BY product_id) AS total_sales_table
    """
                       )

df

highest_sales
0             5

#### Another way to obtain the highest product sales is to sort the result of Query A in descending order and then take the top row.

In [12]:
# Query B'

_, df = dataframe_query(conn,
    """
    SELECT sum(no_of_items) AS highest_sales
    FROM sold_via
    GROUP BY product_id
    ORDER BY highest_sales DESC
    LIMIT 1
    """
                       )

df

highest_sales
0             5

#### We cannot use this trick (sort in descending order and then simply take the top row) to retrieve all the products that have the highest sales, because there can be more than one product.

#### In either case, we have a SELECT command that returns the highest sales, we can use it to select the products whose total sales matches the highest sales. We use the SELECT command in the HAVING clause.

#### Query C below combines Query A and Query B.

In [13]:
# Query C

_, df = dataframe_query(conn,
    """
    SELECT product_id
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = 
        (SELECT max(total_sales) AS highest_sales
         FROM (SELECT sum(no_of_items) AS total_sales
               FROM sold_via
               GROUP BY product_id) AS total_sales_table)
    ORDER BY product_id
    """
                       )

df

product_id
0        3X3
1        4X4

#### Now that we know about views, see how views can simplify the queries.

In [14]:
cursor.execute('DROP VIEW IF EXISTS sales_per_product')

sql = ( """
        CREATE VIEW sales_per_product AS
        SELECT product_id, sum(no_of_items) AS total_sales
        FROM sold_via
        GROUP BY product_id
        """
      )

cursor.execute(sql)

_, df = dataframe_query(conn, 'SELECT * FROM sales_per_product')
df

product_id total_sales
0        1X1           2
1        2X2           3
2        3X3           5
3        4X4           5
4        5X5           2
5        6X6           1

In [15]:
cursor.execute('DROP VIEW IF EXISTS highest_sales')

sql = ( """
        CREATE VIEW highest_sales AS
        SELECT max(total_sales) AS highest_sales
        FROM sales_per_product
        """
      )

cursor.execute(sql)

_, df = dataframe_query(conn, 'SELECT * FROM highest_sales')
df

highest_sales
0             5

In [16]:
_, df = dataframe_query(conn,
    """
    SELECT product_id
    FROM sold_via
    GROUP BY product_id
    HAVING SUM(no_of_items) = 
        (SELECT highest_sales FROM highest_sales)
    ORDER BY product_id
    """
                       )

df

product_id
0        3X3
1        4X4

#### **7.** Rewrite the following query using a join instead of the nested query. Your rewritten query should produce the same results.

#### _For each product that has more than three items sold within all sales transactions, retrieve the product ID, product name, and product price._

``` sql
SELECT product_id, product_name, product_price
FROM product
WHERE product_id IN (SELECT product_id
                     FROM sold_via
                     GROUP BY product_id
                     HAVING SUM(no_of_items) > 3)
```

In [17]:
_, df = dataframe_query(conn,
    """
    SELECT p.product_id, product_name, product_price
    FROM product p, sold_via s
    WHERE p.product_id = s.product_id
    GROUP BY p.product_id, p.product_name, p.product_price
    HAVING SUM(s.no_of_items) > 3
    """
                       )

df

product_id product_name product_price
0        3X3    Cosy Sock         15.00
1        4X4    Dura Boot         90.00

#### **8.** Rewrite the following query using a join instead of the nested query. Your rewritten query should produce the same results.

#### _For each product whose items were sold in more than one sales transaction, retrieve the product id, product name and product price._
``` sql
SELECT product_id, product_name, product_price
FROM product
WHERE product_id IN (SELECT product_id
                     FROM sold_via
                     GROUP BY product_id
                     HAVING COUNT(*) > 1)
```

In [18]:
_, df = dataframe_query(conn,
    """
    SELECT p.product_id, product_name, product_price
    FROM product p, sold_via s
    WHERE p.product_id = s.product_id
    GROUP BY p.product_id, p.product_name, p.product_price
    HAVING COUNT(s.tid) > 1
    """
                       )

df

product_id product_name product_price
0        1X1      Zzz Bag        100.00
1        2X2    Easy Boot         70.00
2        4X4    Dura Boot         90.00

In [19]:
cursor.close()
conn.close()